## Устанавливаем библиотки, если их еще нет

In [711]:
#!pip install newspaper3k
#!pip install dostoevsky
#!python -m dostoevsky download fasttext-social-network-model
#! pip install pytorch-pretrained-bert
#! pip install transformers

In [333]:
#!pip install install xgboost

In [83]:
#!pip install optuna

In [22]:
# import nltk
# nltk.download('punkt')

In [148]:
#nltk.download("stopwords")
#nltk.download('vader_lexicon')

## Загрузим нужные библиотеки

In [28]:
import pandas as pd
import numpy as np
import requests
import optuna
import nltk
import pymorphy2
import itertools
import optuna  
import json
import ast

from optuna.integration import LightGBMPruningCallback
from collections import defaultdict
from sklearn.metrics import r2_score
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from tqdm import tqdm
from collections import Counter
from catboost import CatBoostRegressor, EShapCalcType, EFeaturesSelectionAlgorithm
from lightgbm import LGBMRegressor
from newspaper import Article
from catboost import Pool
from optuna.samplers import TPESampler
from dostoevsky.tokenization import RegexTokenizer
from dostoevsky.models import FastTextSocialNetworkModel
from sklearn.model_selection import KFold

# Считываем изначальный датасет

In [286]:
# df_train = pd.read_csv("train.csv")
# df_test = pd.read_csv("test.csv")

## Функция извлечения статьи по url с сайта

In [174]:
# def content_finder(document_id, session):
#     url = ["https://www.rbc.ru/rbcfreenews/"]
#     url.append(document_id[:document_id.find(session)])
#     url.append("?ysclid=")
#     url.append(session)
#     article = Article("".join(url), language='ru')
#     article.download()
#     article.parse()
#     return (article.text, len(article.images))

## Добавляем статьи в датасеты. Работает долго и иногда падает падает, для этого и нужен словарь

In [175]:
# dict_document_id_content = {}
# dict_document_id_num_imgs = {}

In [176]:
# for i in range(len(df_test)):
#     if df_test.document_id.iloc[i] not in dict_document_id_num_imgs:
#         dict_document_id_content[df_test.document_id.iloc[i]] = content_finder(df_test.document_id.iloc[i], df_test.session.iloc[i])[0]
#         dict_document_id_num_imgs[df_test.document_id.iloc[i]] = content_finder(df_test.document_id.iloc[i], df_test.session.iloc[i])[1]

# for i in range(len(df_train)):
#     if df_train.document_id.iloc[i] not in dict_document_id_num_imgs:
#         dict_document_id_content[df_train.document_id.iloc[i]] = content_finder(df_train.document_id.iloc[i], df_train.session.iloc[i])[0]
#         dict_document_id_num_imgs[df_train.document_id.iloc[i]] = content_finder(df_train.document_id.iloc[i], df_train.session.iloc[i])[1]



# Используем встроенные в библиотеку функции для извлечения текста статьи и количества изображений

In [177]:
# df_train["content"] = df_train["document_id"].map(dict_document_id_content)
# df_train["number_of_img"] = df_train["document_id"].map(dict_document_id_num_imgs)

# df_test["content"] = df_test["document_id"].map(dict_document_id_content)
# df_test["number_of_img"] = df_test["document_id"].map(dict_document_id_num_imgs)

# Сохраняем, чтобы больше не загружать статьи

In [178]:
# df_train.to_csv("df_train_new.csv", index=False)
# df_test.to_csv("df_test_new.csv", index=False)

In [298]:
# df_train = pd.read_csv("df_train_new.csv")
# df_test = pd.read_csv("df_test_new.csv")

In [299]:
# df_train.head(1)

# Функция выгрузки текста страницы на сайте рбк

In [300]:
# def content_finder(document_id, session):
#     url = ["https://www.rbc.ru/rbcfreenews/"]
#     url.append(document_id[:document_id.find(session)])
#     url.append("?ysclid=")
#     url.append(session)
#     return requests.get("".join(url)).text

# Ищем количество ключевых слов на странице

In [302]:
# video = []
# http = []
# https = []
# youtube = []
# yandex = []
# png = []
# img = []
# jpg = []
# lens = []
# ru = []
# com = []
# rbk = []
# ok = []
# vk = []
# content_word = []
# link = []
# title_word = []
# media = []
# script = []
# url = []
# href = []
# classs = []
# ppp = []
# www = []
# meta = []
# utm_source = []
# lll = []
# width = []
# height = []
# data = []
# item = []
# rbk_pro = []

# for i in tqdm(range(len(df_train))):
#     text = content_finder(df_train.document_id.iloc[i], df_train.session.iloc[i]).lower()
#     video.append(len([m.start() for m in re.finditer('video', text)]))
#     http.append(len([m.start() for m in re.finditer('http', text)]))
#     https.append(len([m.start() for m in re.finditer('https', text)]))
#     youtube.append(len([m.start() for m in re.finditer('youtube', text)]))
#     yandex.append(len([m.start() for m in re.finditer('yandex', text)]))
#     png.append(len([m.start() for m in re.finditer('png', text)]))
#     img.append(len([m.start() for m in re.finditer('img', text)]))
#     jpg.append(len([m.start() for m in re.finditer('jpg', text)]))
#     lens.append(len(text))
#     ru.append(len([m.start() for m in re.finditer('.ru', text)]))
#     com.append(len([m.start() for m in re.finditer('.com', text)]))
#     rbk.append(len([m.start() for m in re.finditer('s.rbk', text)]))
#     ok.append(len([m.start() for m in re.finditer('ok.ru', text)]))
#     vk.append(len([m.start() for m in re.finditer('vk.com/', text)]))
#     content_word.append(len([m.start() for m in re.finditer('content', text)]))
#     link.append(len([m.start() for m in re.finditer('link', text)]))
#     title_word.append(len([m.start() for m in re.finditer('title', text)]))
#     media.append(len([m.start() for m in re.finditer('media', text)]))
#     script.append(len([m.start() for m in re.finditer('script', text)]))
#     url.append(len([m.start() for m in re.finditer('url', text)]))
#     href.append(len([m.start() for m in re.finditer('href', text)]))
#     classs.append(len([m.start() for m in re.finditer('class', text)]))
#     ppp.append(len([m.start() for m in re.finditer('://', text)]))
#     www.append(len([m.start() for m in re.finditer('www', text)]))
#     meta.append(len([m.start() for m in re.finditer('meta', text)]))
#     utm_source.append(len([m.start() for m in re.finditer('utm_source', text)]))
#     lll.append(len([m.start() for m in re.finditer(' pro-anons__item__header__image', text)]))
#     width.append(len([m.start() for m in re.finditer('width', text)]))
#     height.append(len([m.start() for m in re.finditer('height', text)]))
#     data.append(len([m.start() for m in re.finditer('data', text)]))
#     item.append(len([m.start() for m in re.finditer('item', text)]))
#     rbk_pro.append(len([m.start() for m in re.finditer('читайте на рбк pro', text)]))    

100%|███████████████████████████████████████| 7000/7000 [35:56<00:00,  3.25it/s]


# Обновляем тренировочный датасет

In [303]:
# df_train["video"] = video
# df_train["http"] = http
# df_train["https"] = https
# df_train["youtube"] = youtube
# df_train["yandex"] = yandex
# df_train["png"] = png
# df_train["img"] = img
# df_train["jpg"] = jpg
# df_train["lens"] = lens
# df_train["ru"] = ru
# df_train["com"] = com
# df_train["rbk"] = rbk
# df_train["ok"] = ok
# df_train["vk"] = vk
# df_train["content_word"] = content_word
# df_train["link"] = link
# df_train["title_word"] = title_word
# df_train["media"] = media
# df_train["script"] = script
# df_train["url"] = url
# df_train["href"] = href
# df_train["classs"] = classs
# df_train["ppp"] = ppp
# df_train["www"] = www
# df_train["meta"] = meta
# df_train["utm_source"] = utm_source
# df_train["lll"] = lll
# df_train["width"] = width
# df_train["height"] = height
# df_train["data"] = data
# df_train["item"] = item
# df_train["rbk_pro_2"] = rbk_pro


# И аналогично для тестового

In [304]:
# video = []
# http = []
# https = []
# youtube = []
# yandex = []
# png = []
# img = []
# jpg = []
# lens = []
# ru = []
# com = []
# rbk = []
# ok = []
# vk = []
# content_word = []
# link = []
# title_word = []
# media = []
# script = []
# url = []
# href = []
# classs = []
# ppp = []
# www = []
# meta = []
# utm_source = []
# lll = []
# width = []
# height = []
# data = []
# item = []
# rbk_pro = []

# for i in tqdm(range(len(df_test))):
#     text = content_finder(df_test.document_id.iloc[i], df_test.session.iloc[i]).lower()
#     video.append(len([m.start() for m in re.finditer('video', text)]))
#     http.append(len([m.start() for m in re.finditer('http', text)]))
#     https.append(len([m.start() for m in re.finditer('https', text)]))
#     youtube.append(len([m.start() for m in re.finditer('youtube', text)]))
#     yandex.append(len([m.start() for m in re.finditer('yandex', text)]))
#     png.append(len([m.start() for m in re.finditer('png', text)]))
#     img.append(len([m.start() for m in re.finditer('img', text)]))
#     jpg.append(len([m.start() for m in re.finditer('jpg', text)]))
#     lens.append(len(text))
#     ru.append(len([m.start() for m in re.finditer('.ru', text)]))
#     com.append(len([m.start() for m in re.finditer('.com', text)]))
#     rbk.append(len([m.start() for m in re.finditer('s.rbk', text)]))
#     ok.append(len([m.start() for m in re.finditer('ok.ru', text)]))
#     vk.append(len([m.start() for m in re.finditer('vk.com/', text)]))
#     content_word.append(len([m.start() for m in re.finditer('content', text)]))
#     link.append(len([m.start() for m in re.finditer('link', text)]))
#     title_word.append(len([m.start() for m in re.finditer('title', text)]))
#     media.append(len([m.start() for m in re.finditer('media', text)]))
#     script.append(len([m.start() for m in re.finditer('script', text)]))
#     url.append(len([m.start() for m in re.finditer('url', text)]))
#     href.append(len([m.start() for m in re.finditer('href', text)]))
#     classs.append(len([m.start() for m in re.finditer('class', text)]))
#     ppp.append(len([m.start() for m in re.finditer('://', text)]))
#     www.append(len([m.start() for m in re.finditer('www', text)]))
#     meta.append(len([m.start() for m in re.finditer('meta', text)]))
#     utm_source.append(len([m.start() for m in re.finditer('utm_source', text)]))
#     lll.append(len([m.start() for m in re.finditer(' pro-anons__item__header__image', text)]))
#     width.append(len([m.start() for m in re.finditer('width', text)]))
#     height.append(len([m.start() for m in re.finditer('height', text)]))
#     data.append(len([m.start() for m in re.finditer('data', text)]))
#     item.append(len([m.start() for m in re.finditer('item', text)]))
#     rbk_pro.append(len([m.start() for m in re.finditer('читайте на рбк pro', text)])) 
    
# df_test["video"] = video
# df_test["http"] = http
# df_test["https"] = https
# df_test["youtube"] = youtube
# df_test["yandex"] = yandex
# df_test["png"] = png
# df_test["img"] = img
# df_test["jpg"] = jpg
# df_test["lens"] = lens
# df_test["ru"] = ru
# df_test["com"] = com
# df_test["rbk"] = rbk
# df_test["ok"] = ok
# df_test["vk"] = vk
# df_test["content_word"] = content_word
# df_test["link"] = link
# df_test["title_word"] = title_word
# df_test["media"] = media
# df_test["script"] = script
# df_test["url"] = url
# df_test["href"] = href
# df_test["classs"] = classs
# df_test["ppp"] = ppp
# df_test["www"] = www
# df_test["meta"] = meta
# df_test["utm_source"] = utm_source
# df_test["lll"] = lll
# df_test["width"] = width
# df_test["height"] = height
# df_test["data"] = data
# df_test["item"] = item
# df_test["rbk_pro_2"] = rbk_pro


100%|███████████████████████████████████████| 3000/3000 [15:38<00:00,  3.20it/s]


# Снова сохраняем датасеты

In [322]:
# df_train.to_csv("df_train_new3.csv", index=False)
# df_test.to_csv("df_test_new3.csv", index=False)

In [2]:
df_train = pd.read_csv("df_train_new3.csv")
df_test = pd.read_csv("df_test_new3.csv")

In [3]:
df_train.head(1)

document_id  \
0  624ac09c9a7947db3d80c98eIDE7mtH4RBqGn-8MXfGffQ   

                                               title         publish_date  \
0  Европейский банк развития приостановил доступ ...  2022-04-04 10:29:44   

                  session authors   ctr                  category  \
0  IDE7mtH4RBqGn-8MXfGffQ      []  1.58  5409f11ce063da9c8b588a18   

                                                tags  views  depth  ...  data  \
0  ['55928d339a794751dc8303d6', '542d1e28cbb20f86...  20460  1.134  ...   350   

  item  rbk_pro_2  num_char  num_words  \
0  574          1      2949        425   

                                       clear_content  clear_num_char  \
0  В заявлении банка говорится: «Ни в одной из эт...            1861   

   clear_num_words  is_rbk_pro  title_word  
0              255           1          90  

[1 rows x 51 columns]

# Замена строк с процентом выше 100 на медиану. Процент не может быть больше 100 

In [4]:
df_train.loc[df_train[df_train.full_reads_percent > 100].index, "full_reads_percent"] = df_train.full_reads_percent.median()

In [5]:
df_train.head(2)

document_id  \
0  624ac09c9a7947db3d80c98eIDE7mtH4RBqGn-8MXfGffQ   
1  620f6b899a7947701cf489e1KtVJsteHStO5oditt3Uvzw   

                                               title         publish_date  \
0  Европейский банк развития приостановил доступ ...  2022-04-04 10:29:44   
1  Кремль назвал регулярным процессом учебные зап...  2022-02-18 10:00:39   

                  session                                            authors  \
0  IDE7mtH4RBqGn-8MXfGffQ                                                 []   
1  KtVJsteHStO5oditt3Uvzw  ['54244e01cbb20f03076b236d','5878a2ec9a7947e53...   

     ctr                  category  \
0  1.580  5409f11ce063da9c8b588a18   
1  1.853  5409f11ce063da9c8b588a12   

                                                tags  views  depth  ...  data  \
0  ['55928d339a794751dc8303d6', '542d1e28cbb20f86...  20460  1.134  ...   350   
1  ['549d25df9a794775979561d2', '58abcf539a7947f1...  19038  1.142  ...   344   

  item  rbk_pro_2  num_char  num_words  \
0  574          1      2949        425   
1  491          0      1780        248   

                                       clear_content  clear_num_char  \
0  В заявлении банка говорится: «Ни в одной из эт...            1861   
1  Все страны, которым положено знать об учениях,...            1780   

   clear_num_words  is_rbk_pro  title_word  
0              255           1          90  
1              248           0          80  

[2 rows x 51 columns]

# Поиск наличия рекламы РБК Pro и удаления ее из текста статьи

In [6]:
def delete_rbk_pro(text):
    start = False
    start = text.find("Читайте на РБК Pro")
    tmp = text[start:]
    if start:
        for stop, value in enumerate(tmp):
            if value == '\n':
                break
        return text[:start] + text[start+stop:]
    else:
        return text
    
def is_rbk_pro(text):
    if text.find("Читайте на РБК Pro") != -1:
        return 1
    else:
        return 0

In [7]:
df_train["num_char"] = df_train.content.apply(lambda x: len(x))
df_test["num_char"] = df_test.content.apply(lambda x: len(x))

df_train["num_words"] = df_train.content.apply(lambda x: len(x.split()))
df_test["num_words"] = df_test.content.apply(lambda x: len(x.split()))    

df_train["clear_content"] = df_train.content.apply(lambda x: delete_rbk_pro(x))
df_test["clear_content"] = df_test.content.apply(lambda x: delete_rbk_pro(x))

df_train["clear_num_char"] = df_train.clear_content.apply(lambda x: len(x))
df_test["clear_num_char"] = df_test.clear_content.apply(lambda x: len(x))

df_train["clear_num_words"] = df_train.clear_content.apply(lambda x: len(x.split()))
df_test["clear_num_words"] = df_test.clear_content.apply(lambda x: len(x.split()))  

df_train["is_rbk_pro"] = df_train.content.apply(lambda x: is_rbk_pro(x))
df_test["is_rbk_pro"] = df_test.content.apply(lambda x: is_rbk_pro(x))

df_train["num_char_title"] = df_train.title.apply(lambda x: len(x))
df_test["num_char_title"] = df_test.title.apply(lambda x: len(x))

df_train["num_words_title"] = df_train.title.apply(lambda x: len(x.split()))
df_test["num_words_title"] = df_test.title.apply(lambda x: len(x.split()))   

In [8]:
df_train["mean_word_length"] = df_train.clear_content.apply(lambda x: np.mean([len(w) for w in x.split()]))
df_test["mean_word_length"] = df_test.clear_content.apply(lambda x: np.mean([len(w) for w in x.split()]))

# Поиск числа стоп слов и их доля относительно всех слов

In [9]:
stopwords = set(nltk.corpus.stopwords.words(["russian", "english"]))

def stop_word_counter(text):
    c = 0
    for word in text.lower().split():
        if word in stopwords:
            c += 1
    return c

def stop_word_ratio(text):
    c = 0
    for word in text.lower().split():
        if word in stopwords:
            c += 1
    return c / len(text.lower().split())

df_train["num_stop_words"] = df_train.clear_content.apply(lambda x: stop_word_counter(x))
df_test["num_stop_words"] = df_test.clear_content.apply(lambda x: stop_word_counter(x))

df_train["ratio_stop_words"] = df_train.clear_content.apply(lambda x: stop_word_ratio(x))
df_test["ratio_stop_words"] = df_test.clear_content.apply(lambda x: stop_word_ratio(x))

# Определение тональностей текста. Если возникнут проблемы с установкой библиотеки, можно удалить, прибавку к скору это практически не дало

In [10]:
tokenizer = RegexTokenizer()
model = FastTextSocialNetworkModel(tokenizer=tokenizer)

results = model.predict(df_train.title, k=6)
positive = []
neutral = []
negative = []
speech = []
skip = []
for sentiment in results:
    positive.append(sentiment["positive"])
    neutral.append(sentiment["neutral"])
    negative.append(sentiment["negative"])
    speech.append(sentiment["speech"])
    skip.append(sentiment["skip"])
df_train["positive_title"] = positive
df_train["neutral_title"] = neutral
df_train["negative_title"] = negative
df_train["speech_title"] = speech
df_train["skip_title"] = skip

results = model.predict(df_test.title, k=6)
positive = []
neutral = []
negative = []
speech = []
skip = []
for sentiment in results:
    positive.append(sentiment["positive"])
    neutral.append(sentiment["neutral"])
    negative.append(sentiment["negative"])
    speech.append(sentiment["speech"])
    skip.append(sentiment["skip"])
df_test["positive_title"] = positive
df_test["neutral_title"] = neutral
df_test["negative_title"] = negative
df_test["speech_title"] = speech
df_test["skip_title"] = skip

results = model.predict(df_train.clear_content, k=6)
positive = []
neutral = []
negative = []
speech = []
skip = []
for sentiment in results:
    positive.append(sentiment["positive"])
    neutral.append(sentiment["neutral"])
    negative.append(sentiment["negative"])
    speech.append(sentiment["speech"])
    skip.append(sentiment["skip"])
df_train["positive_clear_content"] = positive
df_train["neutral_clear_content"] = neutral
df_train["negative_clear_content"] = negative
df_train["speech_clear_content"] = speech
df_train["skip_clear_content"] = skip

results = model.predict(df_test.clear_content, k=6)
positive = []
neutral = []
negative = []
speech = []
skip = []
for sentiment in results:
    positive.append(sentiment["positive"])
    neutral.append(sentiment["neutral"])
    negative.append(sentiment["negative"])
    speech.append(sentiment["speech"])
    skip.append(sentiment["skip"])
df_test["positive_clear_content"] = positive
df_test["neutral_clear_content"] = neutral
df_test["negative_clear_content"] = negative
df_test["speech_clear_content"] = speech
df_test["skip_clear_content"] = skip


In [11]:
df_test.head(2)

document_id  \
0  61f9569a9a794794245a82abJ0AvX96vTAaQCiWVbzoMdw   
1  628c22b89a79470e553f594bQS5CqzXYRnmDdR2LaSreEw   

                                               title         publish_date  \
0  «Крайне провокационная тема»: как Россия и США...  2022-02-01 17:02:44   
1  Власти Херсонской области пообещали сделать ру...  2022-05-24 00:50:55   

                  session authors    ctr                  category  \
0  J0AvX96vTAaQCiWVbzoMdw      []  0.000  5409f11ce063da9c8b588a12   
1  QS5CqzXYRnmDdR2LaSreEw      []  1.598  5409f11ce063da9c8b588a12   

                                                tags  \
0  ['58ca77679a794700b1e37f0a', '5409f1b7e063daa0...   
1  ['5433603acbb20f6e5def0cc5', '5409f420e063daa0...   

                                             content  number_of_img  ...  \
0  WP: между постпредами России и США в ООН произ...              6  ...   
1  Русский станет основным языком для «всех вопро...             18  ...   

   positive_title  neutral_title  negative_title  speech_title  skip_title  \
0        0.039649       0.939923        0.036230      0.000356    0.025967   
1        0.006108       0.928419        0.069552      0.005230    0.043376   

   positive_clear_content  neutral_clear_content  negative_clear_content  \
0                0.056662               0.743178                0.268951   
1                0.044691               0.718604                0.196836   

   speech_clear_content  skip_clear_content  
0              0.006108            0.087574  
1              0.019134            0.075868  

[2 rows x 63 columns]

# Парсинг категории

In [12]:
i = 0
dict_categories = {}
for category in df_train.category.unique():
    dict_categories[category] = i
    i += 1

In [13]:
df_train["category"] = df_train["category"].map(dict_categories)
df_test["category"] = df_test["category"].map(dict_categories)

# Численное представление дней , недель, месяцев, а также часов и минут

In [14]:
df_train['day'] = pd.to_datetime(df_train['publish_date']).dt.strftime("%d").astype(int)
df_train['mounth'] = pd.to_datetime(df_train['publish_date']).dt.strftime("%m").astype(int)

df_test['day'] = pd.to_datetime(df_test['publish_date']).dt.strftime("%d").astype(int)
df_test['mounth'] = pd.to_datetime(df_test['publish_date']).dt.strftime("%m").astype(int)

In [15]:
df_train['day_of_week'] = pd.to_datetime(df_train['publish_date']).dt.strftime("%A")
df_train["day_of_week"] = df_train["day_of_week"].astype('category')
df_train["day_of_week"] = df_train["day_of_week"].cat.codes
df_train["day_of_week"] = df_train["day_of_week"].astype('int')
df_train['hour'] = pd.to_datetime(df_train['publish_date']).dt.strftime("%H").astype(int)
df_train['minute'] = pd.to_datetime(df_train['publish_date']).dt.strftime("%M").astype(int)

df_test['day_of_week'] = pd.to_datetime(df_test['publish_date']).dt.strftime("%A")
df_test["day_of_week"] = df_test["day_of_week"].astype('category')
df_test["day_of_week"] = df_test["day_of_week"].cat.codes
df_test["day_of_week"] = df_test["day_of_week"].astype('int')
df_test['hour'] = pd.to_datetime(df_test['publish_date']).dt.strftime("%H").astype(int)
df_test['minute'] = pd.to_datetime(df_test['publish_date']).dt.strftime("%M").astype(int)

# Медиана, среднее и стандартная ошибка искомых переменных относительно дня, недели или месяца. Считается по трейну и подставляется в тест

In [16]:
#views
df_train['dt'] = pd.to_datetime(df_train['publish_date'])
df_train['week_scale'] = df_train.dt.dt.to_period('W').apply(lambda r: r.start_time)
df_train['month_scale'] = df_train.dt.dt.to_period('M').apply(lambda r: r.start_time)
df_train['day_scale'] = df_train.dt.dt.to_period('D').apply(lambda r: r.start_time)

df_train['week_median_views'] = df_train.views.groupby(df_train['week_scale']).transform('median')
df_train['week_mean_views'] = df_train.views.groupby(df_train['week_scale']).transform('mean')
df_train['week_std_views'] = df_train.views.groupby(df_train['week_scale']).transform('std')
df_train['month_median_views'] = df_train.views.groupby(df_train['month_scale']).transform('median')
df_train['month_mean_views'] = df_train.views.groupby(df_train['month_scale']).transform('mean')
df_train['month_std_views'] = df_train.views.groupby(df_train['month_scale']).transform('std')
df_train['day_median_views'] = df_train.views.groupby(df_train['day_scale']).transform('median')
df_train['day_mean_views'] = df_train.views.groupby(df_train['day_scale']).transform('mean')
df_train['day_std_views'] = df_train.views.groupby(df_train['day_scale']).transform('std')

df_test['dt'] = pd.to_datetime(df_test['publish_date'])
df_test['week_scale'] = df_test.dt.dt.to_period('W').apply(lambda r: r.start_time)
df_test['month_scale'] = df_test.dt.dt.to_period('M').apply(lambda r: r.start_time)
df_test['day_scale'] = df_test.dt.dt.to_period('D').apply(lambda r: r.start_time)

df_test['week_median_views'] = df_test.week_scale.map(df_train.views.groupby(df_train['week_scale']).median())
df_test['week_mean_views'] = df_test.week_scale.map(df_train.views.groupby(df_train['week_scale']).mean())
df_test['week_std_views'] = df_test.week_scale.map(df_train.views.groupby(df_train['week_scale']).std())
df_test['month_median_views'] = df_test.month_scale.map(df_train.views.groupby(df_train['month_scale']).median())
df_test['month_mean_views'] = df_test.month_scale.map(df_train.views.groupby(df_train['month_scale']).mean())
df_test['month_std_views'] = df_test.month_scale.map(df_train.views.groupby(df_train['month_scale']).std())
df_test['day_median_views'] = df_test.day_scale.map(df_train.views.groupby(df_train['day_scale']).median())
df_test['day_mean_views'] = df_test.day_scale.map(df_train.views.groupby(df_train['day_scale']).mean())
df_test['day_std_views'] = df_test.day_scale.map(df_train.views.groupby(df_train['day_scale']).std())

df_test.month_median_views.fillna(df_train.views.median(), inplace=True)
df_test.month_mean_views.fillna(df_train.views.mean(), inplace=True)
df_test.month_std_views.fillna(df_train.views.std(), inplace=True)
df_test.week_median_views.fillna(df_train.views.median(), inplace=True)
df_test.week_mean_views.fillna(df_train.views.mean(), inplace=True)
df_test.week_std_views.fillna(df_train.views.std(), inplace=True)
df_test.day_median_views.fillna(df_train.views.median(), inplace=True)
df_test.day_mean_views.fillna(df_train.views.mean(), inplace=True)
df_test.day_std_views.fillna(df_train.views.std(), inplace=True)

In [17]:
#depth

df_train['week_median_depth'] = df_train.depth.groupby(df_train['week_scale']).transform('median')
df_train['week_mean_depth'] = df_train.depth.groupby(df_train['week_scale']).transform('mean')
df_train['week_std_depth'] = df_train.depth.groupby(df_train['week_scale']).transform('std')
df_train['month_median_depth'] = df_train.depth.groupby(df_train['month_scale']).transform('median')
df_train['month_mean_depth'] = df_train.depth.groupby(df_train['month_scale']).transform('mean')
df_train['month_std_depth'] = df_train.depth.groupby(df_train['month_scale']).transform('std')
df_train['day_median_depth'] = df_train.depth.groupby(df_train['day_scale']).transform('median')
df_train['day_mean_depth'] = df_train.depth.groupby(df_train['day_scale']).transform('mean')
df_train['day_std_depth'] = df_train.depth.groupby(df_train['day_scale']).transform('std')

df_test['week_median_depth'] = df_test.week_scale.map(df_train.depth.groupby(df_train['week_scale']).median())
df_test['week_mean_depth'] = df_test.week_scale.map(df_train.depth.groupby(df_train['week_scale']).mean())
df_test['week_std_depth'] = df_test.week_scale.map(df_train.depth.groupby(df_train['week_scale']).std())
df_test['month_median_depth'] = df_test.month_scale.map(df_train.depth.groupby(df_train['month_scale']).median())
df_test['month_mean_depth'] = df_test.month_scale.map(df_train.depth.groupby(df_train['month_scale']).mean())
df_test['month_std_depth'] = df_test.month_scale.map(df_train.depth.groupby(df_train['month_scale']).std())
df_test['day_median_depth'] = df_test.day_scale.map(df_train.depth.groupby(df_train['day_scale']).median())
df_test['day_mean_depth'] = df_test.day_scale.map(df_train.depth.groupby(df_train['day_scale']).mean())
df_test['day_std_depth'] = df_test.day_scale.map(df_train.depth.groupby(df_train['day_scale']).std())

df_test.month_median_depth.fillna(df_train.depth.median(), inplace=True)
df_test.month_mean_depth.fillna(df_train.depth.mean(), inplace=True)
df_test.month_std_depth.fillna(df_train.depth.std(), inplace=True)
df_test.week_median_depth.fillna(df_train.depth.median(), inplace=True)
df_test.week_mean_depth.fillna(df_train.depth.mean(), inplace=True)
df_test.week_std_depth.fillna(df_train.depth.std(), inplace=True)
df_test.day_median_depth.fillna(df_train.depth.median(), inplace=True)
df_test.day_mean_depth.fillna(df_train.depth.mean(), inplace=True)
df_test.day_std_depth.fillna(df_train.depth.std(), inplace=True)

In [18]:
#full_reads_percent

df_train['week_median_full_reads_percent'] = df_train.full_reads_percent.groupby(df_train['week_scale']).transform('median')
df_train['week_mean_full_reads_percent'] = df_train.full_reads_percent.groupby(df_train['week_scale']).transform('mean')
df_train['week_std_full_reads_percent'] = df_train.full_reads_percent.groupby(df_train['week_scale']).transform('std')
df_train['month_median_full_reads_percent'] = df_train.full_reads_percent.groupby(df_train['month_scale']).transform('median')
df_train['month_mean_full_reads_percent'] = df_train.full_reads_percent.groupby(df_train['month_scale']).transform('mean')
df_train['month_std_full_reads_percent'] = df_train.full_reads_percent.groupby(df_train['month_scale']).transform('std')
df_train['day_median_full_reads_percent'] = df_train.full_reads_percent.groupby(df_train['day_scale']).transform('median')
df_train['day_mean_full_reads_percent'] = df_train.full_reads_percent.groupby(df_train['day_scale']).transform('mean')
df_train['day_std_full_reads_percent'] = df_train.full_reads_percent.groupby(df_train['day_scale']).transform('std')

df_test['week_median_full_reads_percent'] = df_test.week_scale.map(df_train.full_reads_percent.groupby(df_train['week_scale']).median())
df_test['week_mean_full_reads_percent'] = df_test.week_scale.map(df_train.full_reads_percent.groupby(df_train['week_scale']).mean())
df_test['week_std_full_reads_percent'] = df_test.week_scale.map(df_train.full_reads_percent.groupby(df_train['week_scale']).std())
df_test['month_median_full_reads_percent'] = df_test.month_scale.map(df_train.full_reads_percent.groupby(df_train['month_scale']).median())
df_test['month_mean_full_reads_percent'] = df_test.month_scale.map(df_train.full_reads_percent.groupby(df_train['month_scale']).mean())
df_test['month_std_full_reads_percent'] = df_test.month_scale.map(df_train.full_reads_percent.groupby(df_train['month_scale']).std())
df_test['day_median_full_reads_percent'] = df_test.day_scale.map(df_train.full_reads_percent.groupby(df_train['day_scale']).median())
df_test['day_mean_full_reads_percent'] = df_test.day_scale.map(df_train.full_reads_percent.groupby(df_train['day_scale']).mean())
df_test['day_std_full_reads_percent'] = df_test.day_scale.map(df_train.full_reads_percent.groupby(df_train['day_scale']).std())

df_test.month_median_full_reads_percent.fillna(df_train.full_reads_percent.median(), inplace=True)
df_test.month_mean_full_reads_percent.fillna(df_train.full_reads_percent.mean(), inplace=True)
df_test.month_std_full_reads_percent.fillna(df_train.full_reads_percent.std(), inplace=True)
df_test.week_median_full_reads_percent.fillna(df_train.full_reads_percent.median(), inplace=True)
df_test.week_mean_full_reads_percent.fillna(df_train.full_reads_percent.mean(), inplace=True)
df_test.week_std_full_reads_percent.fillna(df_train.full_reads_percent.std(), inplace=True)
df_test.day_median_full_reads_percent.fillna(df_train.full_reads_percent.median(), inplace=True)
df_test.day_mean_full_reads_percent.fillna(df_train.full_reads_percent.mean(), inplace=True)
df_test.day_std_full_reads_percent.fillna(df_train.full_reads_percent.std(), inplace=True)


# Является ли день публикации выходным (например, праздник)

In [21]:
holidays = []
for year in ["2017", "2018", "2019", "2020", "2021", "2022"]:
    url = 'https://raw.githubusercontent.com/d10xa/holidays-calendar/master/json/consultant' + year + '.json'
    r = requests.get(url)
    cal = json.loads(r.text)
    holidays.append(cal["holidays"])

In [22]:
set_holidays = set()
for lst in holidays:
    for el in lst:
        set_holidays.add(el)

is_holiday = []
for date in df_train.publish_date:
    if date[:10] in set_holidays:
        is_holiday.append(1)
    else:
        is_holiday.append(0)
df_train["is_holiday"] = is_holiday  

is_holiday = []
for date in df_test.publish_date:
    if date[:10] in set_holidays:
        is_holiday.append(1)
    else:
        is_holiday.append(0)
df_test["is_holiday"] = is_holiday  

# one-hot encoding тегов и их количество

In [23]:
tags_counter = Counter()
for i in range(len(df_train)):
    tags = df_train.iloc[i].tags
    for character in "',][":
        tags = tags.replace(character, "")
    for tag in tags.split():
        tags_counter[tag] += 1

In [24]:
list_of_most_common_tags = []
for tag in tags_counter:
    list_of_most_common_tags.append(tag)
    
df_train[list_of_most_common_tags] = 0
df_test[list_of_most_common_tags] = 0
set_of_most_common_tags = set(list_of_most_common_tags)

/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_train[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_train[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, whi

/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_train[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_train[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, whi

/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_train[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_train[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, whi

/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_train[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_train[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, whi

/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_train[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_train[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, whi

...

/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_test[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_test[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which

/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_test[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_test[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which

/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_test[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_test[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which

/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_test[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_test[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which

/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_test[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_test[list_of_most_common_tags] = 0
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/928220906.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which

In [25]:
num_tags = []

for i in range(len(df_train)):
    tags = df_train.iloc[i].tags
    for character in "',][":
        tags = tags.replace(character, "")
    for tag in tags.split():
        if tag in set_of_most_common_tags:
            df_train.loc[i, tag] = 1
    num_tags.append(len(tags.split()))
df_train["num_tags"] = num_tags
   
num_tags = []
for i in range(len(df_test)):
    tags = df_test.iloc[i].tags
    for character in "',][":
        tags = tags.replace(character, "")
    for tag in tags.split():
        if tag in set_of_most_common_tags:
            df_test.loc[i, tag] = 1
    num_tags.append(len(tags.split()))
df_test["num_tags"] = num_tags

/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/810301767.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_train["num_tags"] = num_tags
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/810301767.py:22: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_test["num_tags"] = num_tags


In [26]:
df_test.head(2)

document_id  \
0  61f9569a9a794794245a82abJ0AvX96vTAaQCiWVbzoMdw   
1  628c22b89a79470e553f594bQS5CqzXYRnmDdR2LaSreEw   

                                               title         publish_date  \
0  «Крайне провокационная тема»: как Россия и США...  2022-02-01 17:02:44   
1  Власти Херсонской области пообещали сделать ру...  2022-05-24 00:50:55   

                  session authors    ctr  category  \
0  J0AvX96vTAaQCiWVbzoMdw      []  0.000         1   
1  QS5CqzXYRnmDdR2LaSreEw      []  1.598         1   

                                                tags  \
0  ['58ca77679a794700b1e37f0a', '5409f1b7e063daa0...   
1  ['5433603acbb20f6e5def0cc5', '5409f420e063daa0...   

                                             content  number_of_img  ...  \
0  WP: между постпредами России и США в ООН произ...              6  ...   
1  Русский станет основным языком для «всех вопро...             18  ...   

   549b09d29a7947226da749e7  551de9b49a7947486260fdc4  \
0                         0                         0   
1                         0                         0   

   5434e20bcbb20f349505c531  596dbcd49a794737e8577291  \
0                         0                         0   
1                         0                         0   

   5669697c9a7947bfc52ec458  54bfad8f9a794764e0876db2  \
0                         0                         0   
1                         0                         0   

   55928cba9a794751dc82f8dd  59e769a09a794784016dab04  \
0                         0                         0   
1                         0                         0   

   59e769a29a794784016daf86  num_tags  
0                         0         5  
1                         0         4  

[2 rows x 5472 columns]

# Статистика по авторам в разрезе искомых переменных. Для каждой статьи берется суммарная статистика всех авторов, причастных к статье

In [29]:
dict_author_counter = defaultdict(int)

views_of_author = defaultdict(list)
depth_of_author = defaultdict(list)
full_reads_percent_of_author = defaultdict(list)

for i in range(len(df_train.authors)):
    authors = ast.literal_eval(df_train.authors.iloc[i])
    for author in authors:
        dict_author_counter[author] += 1
        views_of_author[author].append(df_train.views.iloc[i])
        depth_of_author[author].append(df_train.depth.iloc[i])
        full_reads_percent_of_author[author].append(df_train.full_reads_percent.iloc[i])

In [30]:
author_pub_number = []
mean_authors_views = []
median_authors_views = []
std_authors_views = []
max_authors_views = []
min_authors_views = []

mean_authors_depth = []
median_authors_depth = []
std_authors_depth = []
max_authors_depth = []
min_authors_depth = []

mean_authors_full_reads_percent = []
median_authors_full_reads_percent = []
std_authors_full_reads_percent = []
max_authors_full_reads_percent = []
min_authors_full_reads_percent = []

for authors in df_train.authors:
    authors = ast.literal_eval(authors)
    tmp = []
    for author in authors:
        tmp.append(dict_author_counter[author])
    if len(tmp) == 0:
        author_pub_number.append(-1)
        mean_authors_views.append(-1)
        median_authors_views.append(-1)
        std_authors_views.append(-1)
        max_authors_views.append(-1)
        min_authors_views.append(-1)
        mean_authors_depth.append(-1)
        median_authors_depth.append(-1)
        std_authors_depth.append(-1)
        max_authors_depth.append(-1)
        min_authors_depth.append(-1)
        mean_authors_full_reads_percent.append(-1)
        median_authors_full_reads_percent.append(-1)
        std_authors_full_reads_percent.append(-1)
        min_authors_full_reads_percent.append(-1)
        max_authors_full_reads_percent.append(-1)
    else:
        author_pub_number.append(sum(tmp) / len(tmp))
        views = list(itertools.chain(*[views_of_author[x] for x in authors]))
        depth = list(itertools.chain(*[depth_of_author[x] for x in authors]))
        full_reads_percent = list(itertools.chain(*[full_reads_percent_of_author[x] for x in authors]))
        mean_authors_views.append(np.mean(views))
        median_authors_views.append(np.median(views))
        std_authors_views.append(np.std(views))
        max_authors_views.append(np.max(views))
        min_authors_views.append(np.min(views))
        mean_authors_depth.append(np.mean(depth))
        median_authors_depth.append(np.median(depth))
        std_authors_depth.append(np.std(depth))
        max_authors_depth.append(np.max(depth))
        min_authors_depth.append(np.min(depth))
        mean_authors_full_reads_percent.append(np.mean(full_reads_percent))
        median_authors_full_reads_percent.append(np.median(full_reads_percent))
        std_authors_full_reads_percent.append(np.std(full_reads_percent))
        min_authors_full_reads_percent.append(np.min(full_reads_percent))
        max_authors_full_reads_percent.append(np.max(full_reads_percent))
        
df_train["author_pub_number"] = author_pub_number

df_train["mean_authors_views"] = mean_authors_views
df_train["median_authors_views"] = median_authors_views
df_train["std_authors_views"] = std_authors_views
df_train["max_authors_views"] = max_authors_views
df_train["min_authors_views"] = min_authors_views

df_train["mean_authors_depth"] = mean_authors_depth
df_train["median_authors_depth"] = median_authors_depth
df_train["std_authors_depth"] = std_authors_depth
df_train["max_authors_depth"] = max_authors_depth
df_train["min_authors_depth"] = min_authors_depth

df_train["mean_authors_full_reads_percent"] = mean_authors_full_reads_percent
df_train["median_authors_full_reads_percent"] = median_authors_full_reads_percent
df_train["std_authors_full_reads_percent"] = std_authors_full_reads_percent
df_train["max_authors_full_reads_percent"] = max_authors_full_reads_percent
df_train["min_authors_full_reads_percent"] = min_authors_full_reads_percent


author_pub_number = []
mean_authors_views = []
median_authors_views = []
std_authors_views = []
max_authors_views = []
min_authors_views = []

mean_authors_depth = []
median_authors_depth = []
std_authors_depth = []
max_authors_depth = []
min_authors_depth = []

mean_authors_full_reads_percent = []
median_authors_full_reads_percent = []
std_authors_full_reads_percent = []
max_authors_full_reads_percent = []
min_authors_full_reads_percent = []

for authors in df_test.authors:
    authors = ast.literal_eval(authors)
    tmp = []
    for author in authors:
        tmp.append(dict_author_counter[author])
    if len(tmp) == 0:
        author_pub_number.append(-1)
        mean_authors_views.append(-1)
        median_authors_views.append(-1)
        std_authors_views.append(-1)
        max_authors_views.append(-1)
        min_authors_views.append(-1)
        mean_authors_depth.append(-1)
        median_authors_depth.append(-1)
        std_authors_depth.append(-1)
        max_authors_depth.append(-1)
        min_authors_depth.append(-1)
        mean_authors_full_reads_percent.append(-1)
        median_authors_full_reads_percent.append(-1)
        std_authors_full_reads_percent.append(-1)
        min_authors_full_reads_percent.append(-1)
        max_authors_full_reads_percent.append(-1)
    else:
        author_pub_number.append(sum(tmp) / len(tmp))
        views = list(itertools.chain(*[views_of_author[x] for x in authors]))
        depth = list(itertools.chain(*[depth_of_author[x] for x in authors]))
        full_reads_percent = list(itertools.chain(*[full_reads_percent_of_author[x] for x in authors]))
        mean_authors_views.append(np.mean(views))
        median_authors_views.append(np.median(views))
        std_authors_views.append(np.std(views))
        max_authors_views.append(np.max(views))
        min_authors_views.append(np.min(views))
        mean_authors_depth.append(np.mean(depth))
        median_authors_depth.append(np.median(depth))
        std_authors_depth.append(np.std(depth))
        max_authors_depth.append(np.max(depth))
        min_authors_depth.append(np.min(depth))
        mean_authors_full_reads_percent.append(np.mean(full_reads_percent))
        median_authors_full_reads_percent.append(np.median(full_reads_percent))
        std_authors_full_reads_percent.append(np.std(full_reads_percent))
        min_authors_full_reads_percent.append(np.min(full_reads_percent))
        max_authors_full_reads_percent.append(np.max(full_reads_percent))
        
df_test["author_pub_number"] = author_pub_number

df_test["mean_authors_views"] = mean_authors_views
df_test["median_authors_views"] = median_authors_views
df_test["std_authors_views"] = std_authors_views
df_test["max_authors_views"] = max_authors_views
df_test["min_authors_views"] = min_authors_views

df_test["mean_authors_depth"] = mean_authors_depth
df_test["median_authors_depth"] = median_authors_depth
df_test["std_authors_depth"] = std_authors_depth
df_test["max_authors_depth"] = max_authors_depth
df_test["min_authors_depth"] = min_authors_depth

df_test["mean_authors_full_reads_percent"] = mean_authors_full_reads_percent
df_test["median_authors_full_reads_percent"] = median_authors_full_reads_percent
df_test["std_authors_full_reads_percent"] = std_authors_full_reads_percent
df_test["max_authors_full_reads_percent"] = max_authors_full_reads_percent
df_test["min_authors_full_reads_percent"] = min_authors_full_reads_percent

/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/1188316025.py:63: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_train["author_pub_number"] = author_pub_number
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/1188316025.py:65: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_train["mean_authors_views"] = mean_authors_views
/var/folders/b5/psvcxmdj5614rwsh5chrp5r9cpv7dl/T/ipykernel_20231/1188316025.py:66: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling 

## Выделим выборки

In [34]:
df_train = df_train.drop(['document_id', 'session', 'tags', 'publish_date', 'content', "title", 'clear_content',  "authors", "dt", "week_scale", "month_scale", "day_scale"], axis=1) 
document_id = df_test.document_id
df_test = df_test.drop(['document_id', 'session', 'tags', 'publish_date', 'content', "title", 'clear_content', "authors", "dt", "week_scale", "month_scale", "day_scale"], axis=1)

In [101]:
df_train.to_csv("df_train_last.csv", index=False)
df_test.to_csv("df_test_last.csv", index=False)

# Для views, depth, full_reads_percent будут разные модели с отличающимся набором выбранных фичей

In [35]:
X = df_train.drop(["views", "depth", "full_reads_percent"], axis = 1)
X_sub = df_test
y1 = df_train["views"]
y2 = df_train["depth"]
y3 = df_train["full_reads_percent"]

# Кросс валидация

In [31]:
# scores = []
# for y in [y1, y2, y3]:
#     cv = KFold(n_splits=4, shuffle=True, random_state=0)
#     cv_scores = np.empty(4)
#     for idx, (train_idx, test_idx) in enumerate(cv.split(X, y)):
#         X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
#         y_train, y_test = y[train_idx], y[test_idx]
#         model = CatBoostRegressor(random_state=0)
#         model.fit(X_train, y_train)
#         preds = model.predict(X_test)
#         cv_scores[idx] = r2_score(y_test, preds)
#     scores.append(np.mean(cv_scores))

# score = 0.4 * scores[0] + 0.3 * scores[1] + 0.3 * scores[2]
# (score, scores[0], scores[1], scores[2])

In [32]:
# (score, scores[0], scores[1], scores[2])

# Тренировка катбуста с дефолтными параметрами. Затем отсев незначащих фичей. Отображены только те, которые используются для построения конкретной модели

In [36]:
X_train = X
y_train = y1
regr1 = CatBoostRegressor(random_state=0)
regr1.fit(X_train, y_train)
pred1 = regr1.predict(X_sub)

y_train = y2
regr2 =  CatBoostRegressor(random_state=0)
regr2.fit(X_train, y_train)
pred2 = regr2.predict(X_sub)

y_train = y3
regr3 = CatBoostRegressor(random_state=0)
regr3.fit(X_train, y_train)
pred3 = regr3.predict(X_sub)

Learning rate set to 0.055186
0:	learn: 92626.5198202	total: 76.4ms	remaining: 1m 16s
1:	learn: 89893.6595470	total: 89.8ms	remaining: 44.8s
2:	learn: 87242.3107375	total: 103ms	remaining: 34.4s
3:	learn: 84765.3854665	total: 128ms	remaining: 31.9s
4:	learn: 82479.1452962	total: 142ms	remaining: 28.2s
5:	learn: 80379.5628876	total: 154ms	remaining: 25.5s
6:	learn: 78170.8409983	total: 166ms	remaining: 23.5s
7:	learn: 76297.8403381	total: 177ms	remaining: 22s
8:	learn: 74400.8493066	total: 189ms	remaining: 20.9s
9:	learn: 72790.8459888	total: 202ms	remaining: 20s
10:	learn: 71068.9352950	total: 211ms	remaining: 18.9s
11:	learn: 69323.5114790	total: 222ms	remaining: 18.3s
12:	learn: 67619.4830297	total: 234ms	remaining: 17.8s
13:	learn: 66127.3654430	total: 246ms	remaining: 17.3s
14:	learn: 64793.4965650	total: 258ms	remaining: 16.9s
15:	learn: 63359.1915114	total: 270ms	remaining: 16.6s
16:	learn: 62059.3201041	total: 282ms	remaining: 16.3s
17:	learn: 60631.7606630	total: 294ms	remainin

163:	learn: 30149.3526352	total: 1.98s	remaining: 10.1s
164:	learn: 30002.4261219	total: 1.99s	remaining: 10.1s
165:	learn: 29981.2100422	total: 2.01s	remaining: 10.1s
166:	learn: 29900.4765140	total: 2.02s	remaining: 10.1s
167:	learn: 29887.3258889	total: 2.03s	remaining: 10s
168:	learn: 29772.7812532	total: 2.04s	remaining: 10s
169:	learn: 29668.5663127	total: 2.05s	remaining: 10s
170:	learn: 29633.8907158	total: 2.06s	remaining: 10s
171:	learn: 29621.5116493	total: 2.07s	remaining: 9.98s
172:	learn: 29609.5483836	total: 2.08s	remaining: 9.96s
173:	learn: 29586.3432331	total: 2.09s	remaining: 9.94s
174:	learn: 29574.2664945	total: 2.1s	remaining: 9.92s
175:	learn: 29562.6993311	total: 2.12s	remaining: 9.91s
176:	learn: 29492.1543505	total: 2.13s	remaining: 9.9s
177:	learn: 29343.2667215	total: 2.14s	remaining: 9.88s
178:	learn: 29232.6744480	total: 2.15s	remaining: 9.86s
179:	learn: 29172.7165822	total: 2.16s	remaining: 9.85s
180:	learn: 29050.7636701	total: 2.17s	remaining: 9.83s
18

321:	learn: 24610.7459604	total: 3.8s	remaining: 8.01s
322:	learn: 24598.3052265	total: 3.82s	remaining: 8s
323:	learn: 24549.8684157	total: 3.83s	remaining: 7.99s
324:	learn: 24505.2084439	total: 3.84s	remaining: 7.98s
325:	learn: 24432.3572243	total: 3.86s	remaining: 7.97s
326:	learn: 24420.8047095	total: 3.87s	remaining: 7.96s
327:	learn: 24415.3047719	total: 3.88s	remaining: 7.95s
328:	learn: 24404.9986169	total: 3.9s	remaining: 7.94s
329:	learn: 24357.1626984	total: 3.91s	remaining: 7.94s
330:	learn: 24296.5044853	total: 3.92s	remaining: 7.93s
331:	learn: 24256.1022089	total: 3.93s	remaining: 7.92s
332:	learn: 24250.6483532	total: 3.95s	remaining: 7.9s
333:	learn: 24241.5134854	total: 3.96s	remaining: 7.89s
334:	learn: 24222.4969728	total: 3.97s	remaining: 7.88s
335:	learn: 24217.1199229	total: 3.98s	remaining: 7.87s
336:	learn: 24207.8753699	total: 3.99s	remaining: 7.86s
337:	learn: 24194.4656325	total: 4s	remaining: 7.84s
338:	learn: 24183.0590354	total: 4.02s	remaining: 7.83s
3

472:	learn: 21813.1431033	total: 5.63s	remaining: 6.27s
473:	learn: 21806.2304848	total: 5.64s	remaining: 6.26s
474:	learn: 21802.6070200	total: 5.65s	remaining: 6.25s
475:	learn: 21795.7310054	total: 5.66s	remaining: 6.24s
476:	learn: 21761.2070031	total: 5.67s	remaining: 6.22s
477:	learn: 21753.6793343	total: 5.69s	remaining: 6.21s
478:	learn: 21744.2972049	total: 5.7s	remaining: 6.2s
479:	learn: 21740.7026941	total: 5.71s	remaining: 6.19s
480:	learn: 21710.0279627	total: 5.72s	remaining: 6.18s
481:	learn: 21657.9321204	total: 5.74s	remaining: 6.17s
482:	learn: 21643.9562217	total: 5.75s	remaining: 6.15s
483:	learn: 21638.9946591	total: 5.76s	remaining: 6.14s
484:	learn: 21635.4062630	total: 5.77s	remaining: 6.13s
485:	learn: 21632.1476864	total: 5.78s	remaining: 6.12s
486:	learn: 21602.5174508	total: 5.79s	remaining: 6.1s
487:	learn: 21592.4348860	total: 5.8s	remaining: 6.09s
488:	learn: 21587.4046314	total: 5.82s	remaining: 6.08s
489:	learn: 21581.3910944	total: 5.83s	remaining: 6.

627:	learn: 19996.2521228	total: 7.47s	remaining: 4.42s
628:	learn: 19974.1168839	total: 7.48s	remaining: 4.41s
629:	learn: 19971.3726726	total: 7.49s	remaining: 4.4s
630:	learn: 19965.1066377	total: 7.5s	remaining: 4.39s
631:	learn: 19962.4015903	total: 7.52s	remaining: 4.38s
632:	learn: 19948.7892703	total: 7.53s	remaining: 4.37s
633:	learn: 19926.0687860	total: 7.54s	remaining: 4.35s
634:	learn: 19923.3563345	total: 7.55s	remaining: 4.34s
635:	learn: 19895.7295782	total: 7.56s	remaining: 4.33s
636:	learn: 19865.1674686	total: 7.58s	remaining: 4.32s
637:	learn: 19862.5517466	total: 7.59s	remaining: 4.3s
638:	learn: 19846.2540373	total: 7.6s	remaining: 4.29s
639:	learn: 19842.1863460	total: 7.61s	remaining: 4.28s
640:	learn: 19822.4369020	total: 7.62s	remaining: 4.27s
641:	learn: 19788.9463026	total: 7.63s	remaining: 4.26s
642:	learn: 19786.2489526	total: 7.64s	remaining: 4.24s
643:	learn: 19778.3473838	total: 7.66s	remaining: 4.23s
644:	learn: 19727.5667817	total: 7.67s	remaining: 4.

...

261:	learn: 5.8956612	total: 3.27s	remaining: 9.22s
262:	learn: 5.8947939	total: 3.28s	remaining: 9.2s
263:	learn: 5.8921512	total: 3.29s	remaining: 9.19s
264:	learn: 5.8875436	total: 3.31s	remaining: 9.17s
265:	learn: 5.8869603	total: 3.32s	remaining: 9.15s
266:	learn: 5.8857907	total: 3.33s	remaining: 9.14s
267:	learn: 5.8824279	total: 3.34s	remaining: 9.13s
268:	learn: 5.8758966	total: 3.35s	remaining: 9.11s
269:	learn: 5.8753680	total: 3.36s	remaining: 9.09s
270:	learn: 5.8744555	total: 3.37s	remaining: 9.07s
271:	learn: 5.8736619	total: 3.39s	remaining: 9.06s
272:	learn: 5.8689265	total: 3.4s	remaining: 9.05s
273:	learn: 5.8657083	total: 3.41s	remaining: 9.03s
274:	learn: 5.8650234	total: 3.42s	remaining: 9.02s
275:	learn: 5.8591503	total: 3.43s	remaining: 9s
276:	learn: 5.8585391	total: 3.44s	remaining: 8.98s
277:	learn: 5.8546755	total: 3.45s	remaining: 8.97s
278:	learn: 5.8541179	total: 3.46s	remaining: 8.96s
279:	learn: 5.8535691	total: 3.48s	remaining: 8.94s
280:	learn: 5.849

423:	learn: 5.5730391	total: 5.12s	remaining: 6.96s
424:	learn: 5.5697399	total: 5.14s	remaining: 6.95s
425:	learn: 5.5654142	total: 5.15s	remaining: 6.94s
426:	learn: 5.5623075	total: 5.16s	remaining: 6.93s
427:	learn: 5.5619094	total: 5.17s	remaining: 6.92s
428:	learn: 5.5612742	total: 5.19s	remaining: 6.9s
429:	learn: 5.5578793	total: 5.2s	remaining: 6.89s
430:	learn: 5.5550421	total: 5.21s	remaining: 6.88s
431:	learn: 5.5546773	total: 5.22s	remaining: 6.86s
432:	learn: 5.5532725	total: 5.23s	remaining: 6.85s
433:	learn: 5.5507935	total: 5.24s	remaining: 6.84s
434:	learn: 5.5481881	total: 5.25s	remaining: 6.82s
435:	learn: 5.5478109	total: 5.26s	remaining: 6.81s
436:	learn: 5.5470274	total: 5.28s	remaining: 6.8s
437:	learn: 5.5447063	total: 5.29s	remaining: 6.78s
438:	learn: 5.5420781	total: 5.3s	remaining: 6.77s
439:	learn: 5.5385206	total: 5.31s	remaining: 6.75s
440:	learn: 5.5368747	total: 5.32s	remaining: 6.74s
441:	learn: 5.5364947	total: 5.33s	remaining: 6.73s
442:	learn: 5.53

594:	learn: 5.2836580	total: 7.17s	remaining: 4.88s
595:	learn: 5.2811588	total: 7.18s	remaining: 4.87s
596:	learn: 5.2808530	total: 7.19s	remaining: 4.85s
597:	learn: 5.2778790	total: 7.2s	remaining: 4.84s
598:	learn: 5.2773709	total: 7.21s	remaining: 4.83s
599:	learn: 5.2770119	total: 7.22s	remaining: 4.82s
600:	learn: 5.2765104	total: 7.23s	remaining: 4.8s
601:	learn: 5.2741686	total: 7.25s	remaining: 4.79s
602:	learn: 5.2738269	total: 7.26s	remaining: 4.78s
603:	learn: 5.2735053	total: 7.27s	remaining: 4.76s
604:	learn: 5.2720751	total: 7.28s	remaining: 4.75s
605:	learn: 5.2715241	total: 7.29s	remaining: 4.74s
606:	learn: 5.2711806	total: 7.3s	remaining: 4.72s
607:	learn: 5.2706973	total: 7.31s	remaining: 4.71s
608:	learn: 5.2687325	total: 7.32s	remaining: 4.7s
609:	learn: 5.2682696	total: 7.33s	remaining: 4.69s
610:	learn: 5.2679808	total: 7.34s	remaining: 4.67s
611:	learn: 5.2651734	total: 7.35s	remaining: 4.66s
612:	learn: 5.2647784	total: 7.36s	remaining: 4.65s
613:	learn: 5.26

765:	learn: 5.0597091	total: 9.22s	remaining: 2.82s
766:	learn: 5.0594282	total: 9.23s	remaining: 2.8s
767:	learn: 5.0589846	total: 9.24s	remaining: 2.79s
768:	learn: 5.0565259	total: 9.25s	remaining: 2.78s
769:	learn: 5.0559180	total: 9.26s	remaining: 2.77s
770:	learn: 5.0537046	total: 9.27s	remaining: 2.75s
771:	learn: 5.0532892	total: 9.29s	remaining: 2.74s
772:	learn: 5.0487278	total: 9.3s	remaining: 2.73s
773:	learn: 5.0484083	total: 9.31s	remaining: 2.72s
774:	learn: 5.0473269	total: 9.32s	remaining: 2.71s
775:	learn: 5.0465882	total: 9.33s	remaining: 2.69s
776:	learn: 5.0460873	total: 9.35s	remaining: 2.68s
777:	learn: 5.0455822	total: 9.36s	remaining: 2.67s
778:	learn: 5.0453230	total: 9.37s	remaining: 2.66s
779:	learn: 5.0450136	total: 9.39s	remaining: 2.65s
780:	learn: 5.0435762	total: 9.4s	remaining: 2.64s
781:	learn: 5.0432782	total: 9.42s	remaining: 2.63s
782:	learn: 5.0429993	total: 9.43s	remaining: 2.61s
783:	learn: 5.0421229	total: 9.44s	remaining: 2.6s
784:	learn: 5.04

927:	learn: 4.8719174	total: 11.5s	remaining: 893ms
928:	learn: 4.8696078	total: 11.5s	remaining: 880ms
929:	learn: 4.8692284	total: 11.5s	remaining: 868ms
930:	learn: 4.8682929	total: 11.5s	remaining: 855ms
931:	learn: 4.8681017	total: 11.6s	remaining: 843ms
932:	learn: 4.8677093	total: 11.6s	remaining: 830ms
933:	learn: 4.8660819	total: 11.6s	remaining: 818ms
934:	learn: 4.8645636	total: 11.6s	remaining: 805ms
935:	learn: 4.8640012	total: 11.6s	remaining: 793ms
936:	learn: 4.8637877	total: 11.6s	remaining: 781ms
937:	learn: 4.8616643	total: 11.6s	remaining: 768ms
938:	learn: 4.8607370	total: 11.6s	remaining: 756ms
939:	learn: 4.8604590	total: 11.7s	remaining: 744ms
940:	learn: 4.8602326	total: 11.7s	remaining: 732ms
941:	learn: 4.8580670	total: 11.7s	remaining: 720ms
942:	learn: 4.8578361	total: 11.7s	remaining: 707ms
943:	learn: 4.8573976	total: 11.7s	remaining: 696ms
944:	learn: 4.8559235	total: 11.8s	remaining: 685ms
945:	learn: 4.8531606	total: 11.8s	remaining: 673ms
946:	learn: 

In [37]:
f_i = pd.DataFrame({'feature_importance': regr1.get_feature_importance(), 
              'feature_names': X.columns}).sort_values(by=['feature_importance'], 
                                                           ascending=False)
X_col_1 = f_i[f_i.feature_importance > 0.01].feature_names

In [38]:
X_col_1.unique()

array(['ctr', 'https', 'http', 'jpg', 'url', 'day_mean_views',
       'month_median_views', 'ppp', 'day_std_views', 'num_stop_words',
       'script', 'mounth', 'href', 'week_mean_full_reads_percent', 'data',
       'video', 'classs', 'day_median_views', 'month_median_depth',
       'positive_title', 'week_median_views',
       'month_median_full_reads_percent', 'hour',
       'month_std_full_reads_percent', 'week_mean_depth',
       'std_authors_views', 'ru', 'day_mean_depth', 'day_std_depth',
       'num_char_title', 'lens', 'num_words', 'num_char',
       '5631bb949a794737108a5623', 'img', 'day', 'yandex', 'meta',
       'month_mean_views', 'skip_title', 'week_std_views',
       'negative_clear_content', 'week_std_depth',
       'month_mean_full_reads_percent', 'day_median_depth',
       '58abcf539a7947f18bc079eb', 'week_mean_views', 'title_word',
       'month_std_depth', 'mean_authors_views',
       'day_std_full_reads_percent', '59e769ab9a794784016dbf12',
       'week_median_dept

In [39]:
f_i1 = pd.DataFrame({'feature_importance': regr2.get_feature_importance(), 
              'feature_names': X.columns}).sort_values(by=['feature_importance'], 
                                                           ascending=False)
X_col_2 = f_i1[f_i1.feature_importance > 0.01].feature_names

In [40]:
X_col_2.unique()

array(['day_median_depth', 'day_mean_depth', 'day_std_depth', 'script',
       'day_mean_views', 'week_mean_depth', 'week_median_depth', 'http',
       'meta', 'ru', 'https', 'ppp', 'ctr', 'title_word', 'url',
       'num_stop_words', 'img', 'hour', 'num_char', 'num_words',
       'clear_num_char', 'jpg', 'day_median_views', 'week_mean_views',
       'is_rbk_pro', 'clear_num_words', 'ratio_stop_words',
       'week_std_full_reads_percent', 'week_std_depth', 'category',
       'month_median_views', 'width', 'day', 'positive_title', 'minute',
       'mean_word_length', 'rbk', 'day_std_full_reads_percent', 'media',
       'std_authors_depth', 'neutral_title', 'www', 'rbk_pro_2',
       'std_authors_views', 'classs', 'min_authors_depth',
       'speech_clear_content', 'month_std_full_reads_percent',
       'min_authors_full_reads_percent', 'content_word', 'speech_title',
       'day_mean_full_reads_percent', 'day_std_views',
       'negative_clear_content', 'negative_title', 'yandex',
    

In [41]:
f_i3 = pd.DataFrame({'feature_importance': regr3.get_feature_importance(), 
              'feature_names': X.columns}).sort_values(by=['feature_importance'], 
                                                           ascending=False)
X_col_3 = f_i3[f_i3.feature_importance > 0.01].feature_names

In [42]:
X_col_3.unique()

array(['clear_num_words', 'clear_num_char', 'num_stop_words', 'ctr',
       'hour', 'num_char', 'title_word', 'category', 'num_words',
       'day_median_full_reads_percent', 'media', 'classs',
       'num_char_title', 'mean_authors_full_reads_percent',
       'week_median_views', 'https', 'url', 'day_mean_full_reads_percent',
       'meta', 'mean_word_length', 'day_std_full_reads_percent',
       'max_authors_full_reads_percent',
       'median_authors_full_reads_percent', 'video', 'std_authors_views',
       'utm_source', 'max_authors_views', 'ratio_stop_words',
       'skip_clear_content', 'week_median_full_reads_percent', 'script',
       'neutral_clear_content', 'img', 'minute', 'day_std_depth',
       'min_authors_full_reads_percent', 'min_authors_views', 'com',
       'mean_authors_depth', 'week_mean_full_reads_percent',
       'positive_title', 'negative_title', 'mean_authors_views',
       'week_mean_depth', 'negative_clear_content', 'skip_title',
       'positive_clear_conten

# Подбор гиперпараметров

In [45]:
# optuna.logging.set_verbosity(optuna.logging.WARNING)

# def objective(trial, X, y):
#     param_grid = {
#         "loss_function": trial.suggest_categorical("loss_function", ["RMSE", "MAE"]),
#         "learning_rate": trial.suggest_categorical("learning_rate", [0.01, 0.014, 0.018, 0.02, 0.05, 0.1, 0.2]),
#         "l2_leaf_reg": trial.suggest_loguniform("l2_leaf_reg", 1e-3, 10),
#         "colsample_bylevel": trial.suggest_float("colsample_bylevel", 0.01, 0.1),
#         "depth": trial.suggest_int("depth", 4, 16),
#         "boosting_type": trial.suggest_categorical("boosting_type", ["Ordered", "Plain"]),
#         "bootstrap_type": trial.suggest_categorical("bootstrap_type", ["Bayesian", "Bernoulli", "MVS"]),
#         "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 2, 300),
#         'n_estimators':  3000
#     }
    
#     if param_grid["bootstrap_type"] == "Bayesian":
#         param_grid["bagging_temperature"] = trial.suggest_float("bagging_temperature", 0, 10)
#     elif param_grid["bootstrap_type"] == "Bernoulli":
#         param_grid["subsample"] = trial.suggest_float("subsample", 0.1, 1)

#     cv = KFold(n_splits=4, shuffle=True, random_state=0)

#     cv_scores = np.empty(4)
#     for idx, (train_idx, test_idx) in enumerate(cv.split(X, y)):
#         X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
#         y_train, y_test = y[train_idx], y[test_idx]

#         model = CatBoostRegressor(thread_count = -1, **param_grid)
#         model.fit(
#             X_train,
#             y_train,
#             eval_set=[(X_test, y_test)],
#             early_stopping_rounds=100,
#             verbose=0
#         )
#         preds = model.predict(X_test)
#         cv_scores[idx] = r2_score(y_test, preds)

#     return np.mean(cv_scores)

In [47]:
# study1 = optuna.create_study(direction="maximize")
# func = lambda trial: objective(trial, X[X_col_1], y1)
# study1.optimize(func, timeout=3600 * 24)

In [48]:
# params_catboost1 = study1.best_trial.params
# study1.best_trial.params

In [49]:
params_catboost1 = {'loss_function': 'RMSE',
 'learning_rate': 0.02,
 'l2_leaf_reg': 0.03833292834584699,
 'colsample_bylevel': 0.09645136485126682,
 'depth': 7,
 'boosting_type': 'Plain',
 'bootstrap_type': 'MVS',
 'min_data_in_leaf': 113}

In [50]:
# study2 = optuna.create_study(direction="maximize")
# func = lambda trial: objective(trial, X[X_col_2], y2)
# study2.optimize(func, timeout=3600 * 12)

In [52]:
# params_catboost2 = study2.best_trial.params
# study2.best_trial.params

In [51]:
params_catboost2 = {'loss_function': 'RMSE',
 'learning_rate': 0.018,
 'l2_leaf_reg': 0.018352788837409116,
 'colsample_bylevel': 0.09582897029692292,
 'depth': 7,
 'boosting_type': 'Plain',
 'bootstrap_type': 'MVS',
 'min_data_in_leaf': 294}

In [53]:
# study3 = optuna.create_study(direction="maximize")
# func = lambda trial: objective(trial, X[X_col_3], y3)
# study3.optimize(func, timeout=3600 * 12)

In [55]:
# params_catboost3 = study3.best_trial.params
# params_catboost3

In [54]:
params_catboost3 = {'loss_function': 'RMSE',
 'learning_rate': 0.02,
 'l2_leaf_reg': 0.020027743792458662,
 'colsample_bylevel': 0.08638837780874961,
 'depth': 15,
 'boosting_type': 'Ordered',
 'bootstrap_type': 'MVS',
 'min_data_in_leaf': 65}

# Итоговая тренировка и предсказание

In [56]:
X_train = X[X_col_1]
y_train = y1
regr1 = CatBoostRegressor(random_state=0, n_estimators=3000, **params_catboost1)
regr1.fit(X_train, y_train)
pred1 = regr1.predict(X_sub[X_col_1])

X_train = X[X_col_2]
y_train = y2
regr2 =  CatBoostRegressor(random_state=0, n_estimators=3000, **params_catboost2)
regr2.fit(X_train, y_train)
pred2 = regr2.predict(X_sub[X_col_2])

X_train = X[X_col_3]
y_train = y3
regr3 = CatBoostRegressor(random_state=0, n_estimators=3000, **params_catboost3)
regr3.fit(X_train, y_train)
pred3 = regr3.predict(X_sub[X_col_3])

Custom logger is already specified. Specify more than one logger at same time is not thread safe.

0:	learn: 94166.6989029	total: 2.8ms	remaining: 8.4s
1:	learn: 92818.3053489	total: 5.77ms	remaining: 8.65s
2:	learn: 91440.9414059	total: 9.02ms	remaining: 9.01s
3:	learn: 90037.0107315	total: 15.6ms	remaining: 11.6s
4:	learn: 88782.1646481	total: 20.8ms	remaining: 12.4s
5:	learn: 87523.4562536	total: 28.1ms	remaining: 14s
6:	learn: 86279.0851500	total: 32ms	remaining: 13.7s
7:	learn: 85063.5501590	total: 34.9ms	remaining: 13s
8:	learn: 83730.0472867	total: 38.3ms	remaining: 12.7s
9:	learn: 82666.9985267	total: 40.3ms	remaining: 12.1s
10:	learn: 81755.8710598	total: 44.4ms	remaining: 12.1s
11:	learn: 80577.8378491	total: 47.8ms	remaining: 11.9s
12:	learn: 79387.9816235	total: 52ms	remaining: 11.9s
13:	learn: 78380.6090510	total: 55.5ms	remaining: 11.8s
14:	learn: 77329.5434104	total: 57.8ms	remaining: 11.5s
15:	learn: 76331.9100152	total: 61.3ms	remaining: 11.4s
16:	learn: 75465.9178082	total: 63.1ms	remaining: 11.1s
17:	learn: 74614.9938640	total: 65.6ms	remaining: 10.9s
18:	learn: 7

189:	learn: 30072.7327994	total: 588ms	remaining: 8.69s
190:	learn: 30040.2465835	total: 591ms	remaining: 8.68s
191:	learn: 29983.4019854	total: 593ms	remaining: 8.67s
192:	learn: 29922.0416653	total: 597ms	remaining: 8.68s
193:	learn: 29881.3290468	total: 600ms	remaining: 8.67s
194:	learn: 29854.7790989	total: 603ms	remaining: 8.67s
195:	learn: 29783.2344257	total: 607ms	remaining: 8.69s
196:	learn: 29729.3316574	total: 611ms	remaining: 8.69s
197:	learn: 29640.3684541	total: 614ms	remaining: 8.69s
198:	learn: 29583.9953921	total: 617ms	remaining: 8.68s
199:	learn: 29504.3355796	total: 620ms	remaining: 8.68s
200:	learn: 29475.0919349	total: 623ms	remaining: 8.68s
201:	learn: 29433.6714923	total: 626ms	remaining: 8.67s
202:	learn: 29375.4410213	total: 629ms	remaining: 8.67s
203:	learn: 29352.4058054	total: 632ms	remaining: 8.66s
204:	learn: 29298.1904659	total: 635ms	remaining: 8.66s
205:	learn: 29255.3778615	total: 638ms	remaining: 8.65s
206:	learn: 29193.2167566	total: 641ms	remaining

388:	learn: 23849.6537324	total: 1.18s	remaining: 7.89s
389:	learn: 23838.1660299	total: 1.18s	remaining: 7.88s
390:	learn: 23823.2499932	total: 1.18s	remaining: 7.88s
391:	learn: 23791.4308479	total: 1.18s	remaining: 7.88s
392:	learn: 23778.9797854	total: 1.19s	remaining: 7.89s
393:	learn: 23767.2690840	total: 1.19s	remaining: 7.89s
394:	learn: 23754.7980661	total: 1.2s	remaining: 7.9s
395:	learn: 23741.2418971	total: 1.2s	remaining: 7.89s
396:	learn: 23724.0834999	total: 1.2s	remaining: 7.9s
397:	learn: 23695.1205945	total: 1.21s	remaining: 7.9s
398:	learn: 23680.0432012	total: 1.22s	remaining: 7.92s
399:	learn: 23632.7223031	total: 1.22s	remaining: 7.92s
400:	learn: 23605.1269974	total: 1.22s	remaining: 7.92s
401:	learn: 23593.0982032	total: 1.22s	remaining: 7.92s
402:	learn: 23572.7785150	total: 1.23s	remaining: 7.91s
403:	learn: 23553.7849705	total: 1.23s	remaining: 7.91s
404:	learn: 23537.8877638	total: 1.23s	remaining: 7.91s
405:	learn: 23525.9987475	total: 1.24s	remaining: 7.91

576:	learn: 20458.5132612	total: 1.75s	remaining: 7.37s
577:	learn: 20450.2420973	total: 1.76s	remaining: 7.37s
578:	learn: 20423.1116745	total: 1.76s	remaining: 7.36s
579:	learn: 20407.3926473	total: 1.76s	remaining: 7.35s
580:	learn: 20381.2980272	total: 1.76s	remaining: 7.35s
581:	learn: 20371.2837948	total: 1.77s	remaining: 7.35s
582:	learn: 20363.2199525	total: 1.77s	remaining: 7.34s
583:	learn: 20351.3884886	total: 1.77s	remaining: 7.34s
584:	learn: 20343.1774946	total: 1.78s	remaining: 7.34s
585:	learn: 20335.3467305	total: 1.78s	remaining: 7.33s
586:	learn: 20319.0065596	total: 1.78s	remaining: 7.33s
587:	learn: 20306.2033532	total: 1.79s	remaining: 7.33s
588:	learn: 20290.7474534	total: 1.79s	remaining: 7.32s
589:	learn: 20275.3983115	total: 1.79s	remaining: 7.32s
590:	learn: 20239.7629776	total: 1.79s	remaining: 7.32s
591:	learn: 20228.6438769	total: 1.8s	remaining: 7.32s
592:	learn: 20212.5048500	total: 1.8s	remaining: 7.31s
593:	learn: 20205.3102617	total: 1.8s	remaining: 7

...

2386:	learn: 3.0914222	total: 1h 34m 42s	remaining: 24m 19s
2387:	learn: 3.0905923	total: 1h 34m 47s	remaining: 24m 17s
2388:	learn: 3.0898840	total: 1h 34m 48s	remaining: 24m 14s
2389:	learn: 3.0893074	total: 1h 34m 50s	remaining: 24m 12s
2390:	learn: 3.0890334	total: 1h 34m 52s	remaining: 24m 9s
2391:	learn: 3.0883721	total: 1h 34m 54s	remaining: 24m 7s
2392:	learn: 3.0876685	total: 1h 34m 57s	remaining: 24m 5s
2393:	learn: 3.0868780	total: 1h 35m	remaining: 24m 2s
2394:	learn: 3.0856913	total: 1h 35m 1s	remaining: 24m
2395:	learn: 3.0852287	total: 1h 35m 4s	remaining: 23m 57s
2396:	learn: 3.0850403	total: 1h 35m 7s	remaining: 23m 55s
2397:	learn: 3.0845533	total: 1h 35m 9s	remaining: 23m 53s
2398:	learn: 3.0837505	total: 1h 35m 12s	remaining: 23m 51s
2399:	learn: 3.0825274	total: 1h 35m 15s	remaining: 23m 48s
2400:	learn: 3.0821426	total: 1h 35m 17s	remaining: 23m 46s
2401:	learn: 3.0816552	total: 1h 35m 19s	remaining: 23m 43s
2402:	learn: 3.0810914	total: 1h 35m 21s	remaining: 23m 

2524:	learn: 2.9777232	total: 1h 40m 27s	remaining: 18m 53s
2525:	learn: 2.9770564	total: 1h 40m 30s	remaining: 18m 51s
2526:	learn: 2.9763502	total: 1h 40m 32s	remaining: 18m 49s
2527:	learn: 2.9761220	total: 1h 40m 34s	remaining: 18m 46s
2528:	learn: 2.9759217	total: 1h 40m 36s	remaining: 18m 44s
2529:	learn: 2.9756544	total: 1h 40m 39s	remaining: 18m 41s
2530:	learn: 2.9753664	total: 1h 40m 41s	remaining: 18m 39s
2531:	learn: 2.9747272	total: 1h 40m 44s	remaining: 18m 37s
2532:	learn: 2.9741848	total: 1h 40m 47s	remaining: 18m 34s
2533:	learn: 2.9738332	total: 1h 40m 49s	remaining: 18m 32s
2534:	learn: 2.9730028	total: 1h 40m 52s	remaining: 18m 30s
2535:	learn: 2.9726786	total: 1h 40m 55s	remaining: 18m 28s
2536:	learn: 2.9724792	total: 1h 40m 58s	remaining: 18m 25s
2537:	learn: 2.9713829	total: 1h 41m	remaining: 18m 23s
2538:	learn: 2.9704578	total: 1h 41m 2s	remaining: 18m 20s
2539:	learn: 2.9668661	total: 1h 41m 4s	remaining: 18m 18s
2540:	learn: 2.9663935	total: 1h 41m 7s	remain

2662:	learn: 2.8820757	total: 1h 46m 23s	remaining: 13m 27s
2663:	learn: 2.8818807	total: 1h 46m 25s	remaining: 13m 25s
2664:	learn: 2.8816462	total: 1h 46m 28s	remaining: 13m 23s
2665:	learn: 2.8803434	total: 1h 46m 29s	remaining: 13m 20s
2666:	learn: 2.8796014	total: 1h 46m 31s	remaining: 13m 18s
2667:	learn: 2.8791878	total: 1h 46m 33s	remaining: 13m 15s
2668:	learn: 2.8789621	total: 1h 46m 36s	remaining: 13m 13s
2669:	learn: 2.8781002	total: 1h 46m 38s	remaining: 13m 10s
2670:	learn: 2.8775463	total: 1h 46m 41s	remaining: 13m 8s
2671:	learn: 2.8772430	total: 1h 46m 43s	remaining: 13m 6s
2672:	learn: 2.8762468	total: 1h 46m 46s	remaining: 13m 3s
2673:	learn: 2.8760650	total: 1h 46m 50s	remaining: 13m 1s
2674:	learn: 2.8739122	total: 1h 46m 53s	remaining: 12m 59s
2675:	learn: 2.8732276	total: 1h 46m 55s	remaining: 12m 56s
2676:	learn: 2.8725055	total: 1h 46m 57s	remaining: 12m 54s
2677:	learn: 2.8716642	total: 1h 47m	remaining: 12m 52s
2678:	learn: 2.8713453	total: 1h 47m 5s	remainin

2801:	learn: 2.7694509	total: 1h 52m 14s	remaining: 7m 55s
2802:	learn: 2.7685398	total: 1h 52m 16s	remaining: 7m 53s
2803:	learn: 2.7684186	total: 1h 52m 18s	remaining: 7m 51s
2804:	learn: 2.7667711	total: 1h 52m 21s	remaining: 7m 48s
2805:	learn: 2.7666529	total: 1h 52m 24s	remaining: 7m 46s
2806:	learn: 2.7661937	total: 1h 52m 26s	remaining: 7m 43s
2807:	learn: 2.7655879	total: 1h 52m 28s	remaining: 7m 41s
2808:	learn: 2.7649914	total: 1h 52m 30s	remaining: 7m 39s
2809:	learn: 2.7645845	total: 1h 52m 33s	remaining: 7m 36s
2810:	learn: 2.7643393	total: 1h 52m 35s	remaining: 7m 34s
2811:	learn: 2.7631112	total: 1h 52m 38s	remaining: 7m 31s
2812:	learn: 2.7618785	total: 1h 52m 40s	remaining: 7m 29s
2813:	learn: 2.7614312	total: 1h 52m 42s	remaining: 7m 26s
2814:	learn: 2.7611024	total: 1h 52m 45s	remaining: 7m 24s
2815:	learn: 2.7605481	total: 1h 52m 49s	remaining: 7m 22s
2816:	learn: 2.7604886	total: 1h 52m 51s	remaining: 7m 19s
2817:	learn: 2.7594533	total: 1h 52m 54s	remaining: 7m 1

2941:	learn: 2.6634120	total: 1h 57m 57s	remaining: 2m 19s
2942:	learn: 2.6627566	total: 1h 58m	remaining: 2m 17s
2943:	learn: 2.6626053	total: 1h 58m 1s	remaining: 2m 14s
2944:	learn: 2.6617937	total: 1h 58m 4s	remaining: 2m 12s
2945:	learn: 2.6614478	total: 1h 58m 5s	remaining: 2m 9s
2946:	learn: 2.6611222	total: 1h 58m 8s	remaining: 2m 7s
2947:	learn: 2.6594174	total: 1h 58m 12s	remaining: 2m 5s
2948:	learn: 2.6590565	total: 1h 58m 14s	remaining: 2m 2s
2949:	learn: 2.6574826	total: 1h 58m 16s	remaining: 2m
2950:	learn: 2.6567756	total: 1h 58m 18s	remaining: 1m 57s
2951:	learn: 2.6560589	total: 1h 58m 22s	remaining: 1m 55s
2952:	learn: 2.6557550	total: 1h 58m 23s	remaining: 1m 53s
2953:	learn: 2.6549325	total: 1h 58m 26s	remaining: 1m 50s
2954:	learn: 2.6547313	total: 1h 58m 27s	remaining: 1m 48s
2955:	learn: 2.6546071	total: 1h 58m 29s	remaining: 1m 45s
2956:	learn: 2.6540776	total: 1h 58m 31s	remaining: 1m 43s
2957:	learn: 2.6521576	total: 1h 58m 34s	remaining: 1m 41s
2958:	learn: 

# Все то же самое, но с LightGBM

In [75]:
X_train = X
y_train = y1
regr11 = LGBMRegressor(random_state=0, n_estimators=5000)
regr11.fit(X_train, y_train)
pred11 = regr11.predict(X_sub)

y_train = y2
regr22 =  LGBMRegressor(random_state=0, n_estimators=5000)
regr22.fit(X_train, y_train)
pred22 = regr22.predict(X_sub)

y_train = y3
regr33 = LGBMRegressor(random_state=0, n_estimators=5000)
regr33.fit(X_train, y_train)
pred33 = regr33.predict(X_sub)

In [76]:
f_i = pd.DataFrame({'feature_importance': regr11.feature_importances_, 
              'feature_names': X.columns}).sort_values(by=['feature_importance'], 
                                                           ascending=False)
X_col_1 = f_i[f_i.feature_importance > 0.01].feature_names

In [77]:
X_col_1.unique()

array(['negative_title', 'positive_title', 'mean_word_length',
       'num_stop_words', 'ratio_stop_words', 'neutral_title',
       'skip_title', 'ctr', 'speech_title', 'minute',
       'positive_clear_content', 'std_authors_views',
       'speech_clear_content', 'day_std_full_reads_percent', 'hour',
       'day', 'negative_clear_content', 'skip_clear_content',
       'num_char_title', 'neutral_clear_content', 'mean_authors_views',
       'ru', 'lens', 'day_std_depth', 'www', 'item', 'num_words',
       'day_mean_full_reads_percent', 'day_median_views',
       'day_median_full_reads_percent', 'num_char', 'day_mean_views',
       '5426c60acbb20f76518c3e4c', 'com', 'day_std_views', 'classs',
       'media', 'clear_num_char', 'num_words_title', 'clear_num_words',
       '5631bb949a794737108a5623', 'day_of_week', 'href',
       '5409f183e063daa0f408ae32', 'data', 'title_word', 'meta',
       'content_word', 'median_authors_views', 'https', 'day_mean_depth',
       'day_median_depth', '5409

In [78]:
f_i = pd.DataFrame({'feature_importance': regr22.feature_importances_, 
              'feature_names': X.columns}).sort_values(by=['feature_importance'], 
                                                           ascending=False)
X_col_2 = f_i[f_i.feature_importance > 0.01].feature_names

In [79]:
X_col_2.unique()

array(['mean_word_length', 'positive_title', 'ratio_stop_words',
       'negative_title', 'skip_title', 'minute', 'neutral_title',
       'speech_title', 'ctr', 'speech_clear_content',
       'negative_clear_content', 'day_std_full_reads_percent',
       'positive_clear_content', 'skip_clear_content',
       'neutral_clear_content', 'num_char_title', 'ru', 'hour', 'lens',
       'www', 'num_stop_words', 'com', 'num_char',
       'day_mean_full_reads_percent', 'day_median_full_reads_percent',
       'day_std_depth', 'day', 'media', 'classs', 'item', 'num_words',
       'clear_num_char', 'https', 'day_median_views', 'day_std_views',
       'clear_num_words', 'day_of_week', 'href', 'day_mean_views', 'png',
       'http', 'num_words_title', 'day_mean_depth', 'day_median_depth',
       'number_of_img', 'content_word', 'link', 'title_word', 'data',
       'ppp', 'meta', 'utm_source', 'author_pub_number', 'num_tags',
       'yandex', 'min_authors_views', 'min_authors_full_reads_percent',
    

In [80]:
f_i = pd.DataFrame({'feature_importance': regr33.feature_importances_, 
              'feature_names': X.columns}).sort_values(by=['feature_importance'], 
                                                           ascending=False)
X_col_3 = f_i[f_i.feature_importance > 0.01].feature_names

In [81]:
X_col_3.unique()

array(['skip_title', 'mean_word_length', 'speech_title', 'negative_title',
       'ratio_stop_words', 'positive_title', 'minute', 'neutral_title',
       'speech_clear_content', 'negative_clear_content', 'ctr',
       'positive_clear_content', 'day_std_full_reads_percent',
       'skip_clear_content', 'neutral_clear_content', 'num_char_title',
       'lens', 'hour', 'www', 'day', 'num_stop_words',
       'day_median_full_reads_percent', 'ru', 'num_char', 'item',
       'day_mean_full_reads_percent', 'day_std_views', 'clear_num_char',
       'num_words', 'day_std_depth', 'com', 'clear_num_words', 'classs',
       'day_mean_views', 'day_median_views', 'media', 'day_of_week',
       'num_words_title', 'href', 'content_word', 'data', 'https', 'link',
       'day_mean_depth', 'day_median_depth', 'http', 'meta', 'title_word',
       'ppp', 'author_pub_number', 'utm_source', 'num_tags',
       '5409f298e063daa0f408b126', 'yandex', '5426c60acbb20f76518c3e4c',
       'min_authors_views', 'week_

In [82]:
# def objective(trial, X, y):
#     param_grid = {
#                 'metric': 'rmse', 
#                 'random_state': 0,
#                 'n_estimators': 5000,
#                 'boosting_type': trial.suggest_categorical("boosting_type", ["gbdt", "goss"]),
#                 'reg_alpha': trial.suggest_loguniform('reg_alpha', 1e-3, 10.0),
#                 'reg_lambda': trial.suggest_loguniform('reg_lambda', 1e-3, 10.0),
#                 'colsample_bytree': trial.suggest_categorical('colsample_bytree', [0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0]),
#                 'subsample': trial.suggest_categorical('subsample', [0.4, 0.5, 0.6, 0.7, 0.85, 1.0]),
#                 'learning_rate': trial.suggest_categorical('learning_rate', [0.002, 0.005, 0.01, 0.03, 0.05]),
#                 'max_depth': trial.suggest_int('max_depth', 2, 16, step=1),
#                 'num_leaves' : trial.suggest_int('num_leaves', 2, 300, step=5),
#                 'min_child_samples': trial.suggest_int('min_child_samples', 1, 300, step=5),
#             }

#     cv = KFold(n_splits=4, shuffle=True, random_state=0)

#     cv_scores = np.empty(4)
#     for idx, (train_idx, test_idx) in enumerate(cv.split(X, y)):
#         X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
#         y_train, y_test = y[train_idx], y[test_idx]

#         model = LGBMRegressor(n_jobs = -1, **param_grid)
#         model.fit(
#             X_train,
#             y_train,
#             eval_set=[(X_test, y_test)],
#             early_stopping_rounds=100,
#             verbose=0
#         )
#         preds = model.predict(X_test)
#         cv_scores[idx] = r2_score(y_test, preds)

#     return np.mean(cv_scores)



In [83]:
# study1 = optuna.create_study(direction="maximize")
# func = lambda trial: objective(trial, X[X_col_1], y1)
# study1.optimize(func, timeout=3600 * 8)

In [84]:
# study1.best_trial.params

In [85]:
params_lgb1 = {'boosting_type': 'goss',
 'reg_alpha': 0.02002980895823484,
 'reg_lambda': 9.859429325824657,
 'colsample_bytree': 0.6,
 'subsample': 1.0,
 'learning_rate': 0.005,
 'max_depth': 7,
 'num_leaves': 137,
 'min_child_samples': 6}

In [86]:
# study2 = optuna.create_study(direction="maximize")
# func = lambda trial: objective(trial, X[X_col_2], y2)
# study2.optimize(func, timeout=3600 * 6)

In [87]:
# study2.best_trial.params

In [88]:
params_lgb2 = {'boosting_type': 'gbdt',
 'reg_alpha': 0.0030250772864869797,
 'reg_lambda': 0.05608335458643468,
 'colsample_bytree': 0.3,
 'subsample': 0.7,
 'learning_rate': 0.005,
 'max_depth': 8,
 'num_leaves': 267,
 'min_child_samples': 16}

In [89]:
# study3 = optuna.create_study(direction="maximize")
# func = lambda trial: objective(trial, X[X_col_3], y3)
# study3.optimize(func, timeout=3600 * 6)

In [90]:
# study3.best_trial.params

In [91]:
params_lgb3 = {'boosting_type': 'gbdt',
 'reg_alpha': 0.0045948660812203355,
 'reg_lambda': 0.017544256851964698,
 'colsample_bytree': 0.3,
 'subsample': 0.5,
 'learning_rate': 0.01,
 'max_depth': 14,
 'num_leaves': 22,
 'min_child_samples': 51}

In [93]:
# на сабмит
X_train = X[X_col_1]
y_train = y1
regr11 = LGBMRegressor(random_state=0, n_estimators=5000, **params_lgb1)
regr11.fit(X_train, y_train)
pred11 = regr11.predict(X_sub[X_col_1])

X_train = X[X_col_2]
y_train = y2
regr22 =  LGBMRegressor(random_state=0, n_estimators=5000, **params_lgb2)
regr22.fit(X_train, y_train)
pred22 = regr22.predict(X_sub[X_col_2])

X_train = X[X_col_3]
y_train = y3
regr33 = LGBMRegressor(random_state=0, n_estimators=5000, **params_lgb3)
regr33.fit(X_train, y_train)
pred33 = regr33.predict(X_sub[X_col_3])

## Submission

In [96]:
sub = pd.DataFrame({"document_id": document_id, 
                    "views": (pred1 + pred11) / 2, 
                    "depth": (pred2 + pred22) / 2, 
                    "full_reads_percent": (pred3 + pred33) / 2})


In [97]:
sub[sub.views < 0]

document_id         views     depth  \
514   626b34599a7947b965f20b160VjrpWPLT8KOu1vLP-U9mg   -929.190330  1.045081   
757   6287d89e9a79477b3c282cddB4kHz4TlQumTxxpF6t4Ghg   -219.087835  1.059765   
869   626308319a79472d6ecfa0d3xtvgxp0pSyOxxRiVMv58ig  -1408.938018  1.045696   
921   629311bb9a794741e69610cf1V1YPTXARfGUCJREqBrKVw   -281.448256  1.057123   
962   626a892f9a79477a0e264792_PICpVQVQz-HF6JxJp-k1w    -33.307590  1.075925   
1178  62379f729a79471983e1280aqkPlGr-qQwO9LmBRDDi76g -11884.877366  1.153678   
1261  6267472d9a7947d11fe0afd1eQYdYzm1SEScLC7Z8kVc0A   -813.198734  1.045120   
1750  626839a59a7947301fc871f8jd9sghyARfuMgcPw3aVR1Q   -594.557482  1.052303   
1807  62370d239a79477ec98eac8db-CkZVdKQgCZVUtagKNCSw  -5618.796597  1.144637   
2089  6280658a9a79478d8c0562b8DRiuWueqTe-_QXsPkY1wPw   -349.008816  1.060600   
2228  625f5aba9a79475f2a9c5c5cwx-5NxjPS2ipDY78UbyMRw   -325.983752  1.050927   
2647  626d65a39a794769d165634esFYxcmMrQh-N4m6kH1KdZA   -241.111863  1.041510   
2701  6261ad9e9a7947ba4b87a14bVZ_xLNYISJ2QL5OL0UPBuQ  -5155.138729  1.043334   
2747  626c29d39a79471ad0e1344fOP-vekeER5SyZdLTVmoYmg   -524.903640  1.043148   

      full_reads_percent  
514            31.413021  
757            28.099342  
869            30.909782  
921            45.053603  
962            34.091314  
1178           35.299415  
1261           33.068242  
1750           24.404046  
1807           32.794688  
2089           45.231465  
2228           35.291503  
2647           36.278202  
2701           21.347562  
2747           27.613166

In [98]:
sub.loc[sub.views < 0, "views"] = 7500

In [99]:
sub[sub.views < 0]

Empty DataFrame
Columns: [document_id, views, depth, full_reads_percent]
Index: []

In [100]:
sub.to_csv("sub.csv", index=False)